# Analyse foncière Inter-Annuel

Importation des librairies et des données ainsi que l'import des dapartements et des régions


In [15]:
import pandas as pd
import numpy as np
import re
import matplotlib.pyplot as plt
import datetime
import json
import folium
import json
import pandas as pd
import numpy as np
from branca.colormap import linear
from datetime import timedelta
from urllib.request import urlopen
import numpy as np
import pandas as pd
from plotly.offline import plot, iplot, init_notebook_mode
init_notebook_mode(connected=True)
import plotly.graph_objects as go
import plotly.express as px
import plotly.subplots as sp
import warnings
warnings.filterwarnings('ignore')

DEPARTMENTS = json.load(open("../data/departements_dict.json"))

REGIONS = json.load(open("../data/regions_dict.json"))

dth = '#ff2e63' 
rec = '#21bf73'
act = '#fe9801'
cnf = '#393e46'

data = pd.read_csv(r"../data/annee_traitee/2018.csv",low_memory=False,sep=",",header=0,index_col=0)
data = data.append(pd.read_csv(r"../data/annee_traitee/2019.csv",low_memory=False,sep=",",header=0,index_col=0))
data = data.append(pd.read_csv(r"../data/annee_traitee/2020.csv",low_memory=False,sep=",",header=0,index_col=0))
data = data.append(pd.read_csv(r"../data/annee_traitee/2021.csv",low_memory=False,sep=",",header=0,index_col=0))
data = data.append(pd.read_csv(r"../data/annee_traitee/2022.csv",low_memory=False,sep=",",header=0,index_col=0))

data["Date mutation"] = pd.to_datetime(data["Date mutation"], format="%Y-%m-%d")
data = data.reset_index(drop=True)

In [7]:
display(data)

Date mutation  Valeur fonciere  No voie Type de voie Code voie  \
0           2018-01-03         109000.0     13.0          RUE      1660   
1           2018-01-03         109000.0     13.0          RUE      1660   
2           2018-01-04         239300.0      4.0          RUE      0025   
3           2018-01-04         239300.0      4.0          RUE      0025   
4           2018-01-04         239300.0      4.0          RUE      0025   
...                ...              ...      ...          ...       ...   
10758898    2022-12-30        3500000.0     19.0          RUE      4879   
10758899    2022-12-19         525000.0      3.0          RUE      3842   
10758900    2022-12-19         525000.0      3.0          RUE      3842   
10758901    2022-12-30          15500.0     69.0          RUE      0679   
10758902    2022-11-21          30000.0     48.0          RUE      8358   

                       Voie  Code postal Code departement  Code commune  \
0               GEN LOGEROT       1000.0                1            53   
1               GEN LOGEROT       1000.0                1            53   
2            DE LA BARMETTE       1250.0                1            95   
3            DE LA BARMETTE       1250.0                1            95   
4            DE LA BARMETTE       1250.0                1            95   
...                     ...          ...              ...           ...   
10758898        JEAN DOLENT      75014.0               75           114   
10758899  FREDERIC MAGISSON      75015.0               75           115   
10758900  FREDERIC MAGISSON      75015.0               75           115   
10758901           BARRAULT      75013.0               75           113   
10758902     DE LA ROQUETTE      75011.0               75           111   

         Section  ...  Surface Carrez du 4eme lot Surface Carrez du 5eme lot  \
0             AN  ...                         NaN                        NaN   
1             AN  ...                         NaN                        NaN   
2             AH  ...                         NaN                        NaN   
3             AH  ...                         NaN                        NaN   
4             AH  ...                         NaN                        NaN   
...          ...  ...                         ...                        ...   
10758898      AS  ...                         NaN                        NaN   
10758899      EJ  ...                         NaN                        NaN   
10758900      EJ  ...                         NaN                        NaN   
10758901      DM  ...                         NaN                        NaN   
10758902      CD  ...                         NaN                        NaN   

          Nombre de lots  Code type local  \
0                      2              2.0   
1                      1              3.0   
2                      0              1.0   
3                      0              1.0   
4                      0              1.0   
...                  ...              ...   
10758898               1              4.0   
10758899               2              3.0   
10758900               2              2.0   
10758901               1              3.0   
10758902               1              3.0   

                                        Type local  Surface reelle bati  \
0                                      Appartement                 73.0   
1                                       Dépendance                  0.0   
2                                           Maison                163.0   
3                                           Maison                163.0   
4                                           Maison                 51.0   
...                                            ...                  ...   
10758898  Local industriel. commercial ou assimilé                327.0   
10758899                                Dépendance                  0.0   
10758900                      

In [8]:
temp = data[(data["Type local"] != "Dépendance")& (data["Type local"] != "Local industriel. commercial ou assimilé")].reset_index(drop = True)
temp["Month mutation"] = temp["Date mutation"].dt.month

temp['Prix mètre carré Paris 2018'] = temp[(temp["Code departement"] == '75')&(temp["Date mutation"].dt.year == 2018)]["Valeur fonciere"]/temp[(temp["Code departement"] == '75')&(temp["Date mutation"].dt.year == 2018)]["Surface reelle bati"]
temp['Prix mètre carré Paris 2019'] = temp[(temp["Code departement"] == '75')&(temp["Date mutation"].dt.year == 2019)]["Valeur fonciere"]/temp[(temp["Code departement"] == '75')&(temp["Date mutation"].dt.year == 2019)]["Surface reelle bati"]
temp['Prix mètre carré Paris 2022'] = temp[(temp["Code departement"] == '75')&(temp["Date mutation"].dt.year == 2022)]["Valeur fonciere"]/temp[(temp["Code departement"] == '75')&(temp["Date mutation"].dt.year == 2022)]["Surface reelle bati"]

temp =temp.replace(np.inf, np.nan)
display(temp['Prix mètre carré Paris 2018'].mean())
display(temp)

# temp['No. of Recovered to 1 Death Case'] = round(temp['Recovered']/temp['Deaths'], 3)
temp = temp.groupby('Month mutation')["Prix mètre carré Paris 2018","Prix mètre carré Paris 2019","Prix mètre carré Paris 2022"].mean().reset_index()

temp = temp.melt(id_vars='Month mutation', value_vars=['Prix mètre carré Paris 2018','Prix mètre carré Paris 2019','Prix mètre carré Paris 2022'], 
                 var_name='Departements', value_name='Value')

fig = px.line(temp, x="Month mutation", y="Value", color='Departements', log_y=True, 
              title='Evolution du prix du mètre carré à paris depuis 2018', color_discrete_sequence=[dth, rec,act])
fig.show()



39946.71816770582

Date mutation  Valeur fonciere  No voie Type de voie Code voie  \
0          2018-01-03         109000.0     13.0          RUE      1660   
1          2018-01-04         239300.0      4.0          RUE      0025   
2          2018-01-04         239300.0      4.0          RUE      0025   
3          2018-01-04         239300.0      4.0          RUE      0025   
4          2018-01-04         239300.0      4.0          RUE      0025   
...               ...              ...      ...          ...       ...   
6507941    2022-12-29        1650000.0     78.0           AV      7149   
6507942    2022-11-03         291000.0    128.0          RUE      0012   
6507943    2022-12-23         934000.0      5.0          VLA      3488   
6507944    2022-12-23          70000.0     67.0          RUE      1255   
6507945    2022-12-19         525000.0      3.0          RUE      3842   

                      Voie  Code postal Code departement  Code commune  \
0              GEN LOGEROT       1000.0                1            53   
1           DE LA BARMETTE       1250.0                1            95   
2           DE LA BARMETTE       1250.0                1            95   
3           DE LA BARMETTE       1250.0                1            95   
4           DE LA BARMETTE       1250.0                1            95   
...                    ...          ...              ...           ...   
6507941        PAUL DOUMER      75016.0               75           116   
6507942   DE L ABBE GROULT      75015.0               75           115   
6507943        FAISANDERIE      75016.0               75           116   
6507944           BRANCION      75015.0               75           115   
6507945  FREDERIC MAGISSON      75015.0               75           115   

        Section  ...   Type local Surface reelle bati  \
0            AN  ...  Appartement                73.0   
1            AH  ...       Maison               163.0   
2            AH  ...       Maison               163.0   
3            AH  ...       Maison                51.0   
4            AH  ...       Maison                51.0   
...         ...  ...          ...                 ...   
6507941      DM  ...  Appartement               150.0   
6507942      AE  ...  Appartement                35.0   
6507943      EE  ...  Appartement                58.0   
6507944      AJ  ...  Appartement                15.0   
6507945      EJ  ...  Appartement                40.0   

         Nombre pieces principales  Nature culture  Surface terrain  \
0                              4.0             NaN              NaN   
1                              4.0               S            949.0   
2                              4.0              AG            420.0   
3                              2.0              AG            420.0   
4                              2.0               S            949.0   
...                            ...             ...              ...   
6507941                        6.0             NaN              NaN   
6507942                        2.0             NaN              NaN   
6507943                        2.0             NaN              NaN   
6507944                        1.0             NaN              NaN   
6507945                        3.0             NaN              NaN   

         Nature mutation  Month mutation  Prix mètre carré Paris 2018  \
0                    NaN               1                          NaN   
1                    NaN               1                          NaN   
2                    NaN               1                          NaN   
3                    NaN               1                          NaN   
4                    NaN               1                          NaN   
...                  ...             ...                          ...   
6507941            Vente              12                          NaN   
6507942     Adjudication              11                          NaN   
6507943          Echange           

In [22]:
temp = data[(data["Type local"] != "Dépendance")& (data["Type local"] != "Local industriel. commercial ou assimilé")].reset_index(drop = True)
temp["Month mutation"] = temp["Date mutation"].dt.month
temp["carrez_sum"] = temp["Surface Carrez du 1er lot"].fillna(0)  +  temp["Surface Carrez du 2eme lot"].fillna(0) + temp["Surface Carrez du 3eme lot"].fillna(0) + temp["Surface Carrez du 4eme lot"].fillna(0) + temp["Surface Carrez du 5eme lot"].fillna(0)
temp["Prix mètre carré"] = np.where(temp["carrez_sum"] != 0,temp["Valeur fonciere"]/temp["carrez_sum"],temp["Valeur fonciere"]/temp["Surface reelle bati"])
temp = temp.drop(np.where(temp['Prix mètre carré'] > 25000)[0])

temp['Prix mètre carré Paris 2018'] = temp[(temp["Code departement"] == '75')&(temp["Date mutation"].dt.year == 2018)]["Prix mètre carré"]
temp['Prix mètre carré Paris 2019'] = temp[(temp["Code departement"] == '75')&(temp["Date mutation"].dt.year == 2019)]["Prix mètre carré"]
temp['Prix mètre carré Paris 2022'] = temp[(temp["Code departement"] == '75')&(temp["Date mutation"].dt.year == 2022)]["Prix mètre carré"]

temp =temp.replace(np.inf, np.nan)
display(temp['Prix mètre carré Paris 2018'].mean())
display(temp)

# temp['No. of Recovered to 1 Death Case'] = round(temp['Recovered']/temp['Deaths'], 3)
temp = temp.groupby('Month mutation')["Prix mètre carré Paris 2018","Prix mètre carré Paris 2019","Prix mètre carré Paris 2022"].mean().reset_index()

temp = temp.melt(id_vars='Month mutation', value_vars=['Prix mètre carré Paris 2018','Prix mètre carré Paris 2019','Prix mètre carré Paris 2022'], 
                 var_name='Departements', value_name='Value')

fig = px.line(temp, x="Month mutation", y="Value", color='Departements', log_y=True, 
              title='Evolution du prix du mètre carré à paris depuis 2018', color_discrete_sequence=[dth, rec,act])
fig.show()


9517.426273610497

Date mutation  Valeur fonciere  No voie Type de voie Code voie  \
0          2018-01-03         109000.0     13.0          RUE      1660   
1          2018-01-04         239300.0      4.0          RUE      0025   
2          2018-01-04         239300.0      4.0          RUE      0025   
3          2018-01-04         239300.0      4.0          RUE      0025   
4          2018-01-04         239300.0      4.0          RUE      0025   
...               ...              ...      ...          ...       ...   
6507941    2022-12-29        1650000.0     78.0           AV      7149   
6507942    2022-11-03         291000.0    128.0          RUE      0012   
6507943    2022-12-23         934000.0      5.0          VLA      3488   
6507944    2022-12-23          70000.0     67.0          RUE      1255   
6507945    2022-12-19         525000.0      3.0          RUE      3842   

                      Voie  Code postal Code departement  Code commune  \
0              GEN LOGEROT       1000.0                1            53   
1           DE LA BARMETTE       1250.0                1            95   
2           DE LA BARMETTE       1250.0                1            95   
3           DE LA BARMETTE       1250.0                1            95   
4           DE LA BARMETTE       1250.0                1            95   
...                    ...          ...              ...           ...   
6507941        PAUL DOUMER      75016.0               75           116   
6507942   DE L ABBE GROULT      75015.0               75           115   
6507943        FAISANDERIE      75016.0               75           116   
6507944           BRANCION      75015.0               75           115   
6507945  FREDERIC MAGISSON      75015.0               75           115   

        Section  ...  Nombre pieces principales Nature culture  \
0            AN  ...                        4.0            NaN   
1            AH  ...                        4.0              S   
2            AH  ...                        4.0             AG   
3            AH  ...                        2.0             AG   
4            AH  ...                        2.0              S   
...         ...  ...                        ...            ...   
6507941      DM  ...                        6.0            NaN   
6507942      AE  ...                        2.0            NaN   
6507943      EE  ...                        2.0            NaN   
6507944      AJ  ...                        1.0            NaN   
6507945      EJ  ...                        3.0            NaN   

         Surface terrain  Nature mutation  Month mutation  carrez_sum  \
0                    NaN              NaN               1        0.00   
1                  949.0              NaN               1        0.00   
2                  420.0              NaN               1        0.00   
3                  420.0              NaN               1        0.00   
4                  949.0              NaN               1        0.00   
...                  ...              ...             ...         ...   
6507941              NaN            Vente              12      154.75   
6507942              NaN     Adjudication              11        0.00   
6507943              NaN          Echange              12        0.00   
6507944              NaN          Echange              12        0.00   
6507945              NaN            Vente              12       46.65   

         Prix mètre carré  Prix mètre carré Paris 2018  \
0             1493.150685                          NaN   
1             1468.098160                          NaN   
2             1468.098160                          NaN   
3             4692.156863                          NaN   
4             4692.156863                          NaN   
...                   ...                          ...   
6507941      10662.358643                          NaN   
6507942       8314.285714                          NaN   
6507943      16103.448276             

In [25]:
def location(row):
    if row['Code departement']=='75':
            return 'Paris'
    elif row['Code departement']=='6':
            return 'Alpes-Maritimes'
    elif row['Code departement']=='59':
        return 'Nord'
    else:
        return 'Reste de la France'


temp = data[(data["Type local"] != "Dépendance")& (data["Type local"] != "Local industriel. commercial ou assimilé")].reset_index(drop = True)
temp['Prix mètre carré'] = temp['Valeur fonciere']/temp['Surface reelle bati']
temp['Region'] = temp.apply(location, axis=1)
temp['Date'] = temp['Date mutation'].dt.strftime('%Y-%m-%d')
temp = temp.groupby(['Region', 'Date'])['Prix mètre carré'].mean().reset_index()
temp = temp.melt(id_vars=['Region', 'Date'], value_vars=['Prix mètre carré'], 
                 var_name='Case', value_name='Count').sort_values('Count')
# temp = temp.sort_values(['Date', 'Region', 'Case']).reset_index()
temp.head()

fig = px.bar(temp, y='Region', x='Count', color='Case', barmode='group', orientation='h',
             text='Count', title='Hubei - China - World', animation_frame='Date',
             color_discrete_sequence= [dth, rec, cnf], range_x=[0, 70000])
fig.update_traces(textposition='outside')
# fig.update_layout(uniformtext_minsize=8, uniformtext_mode='hide')
# fig.update_layout(yaxis={'categoryorder':'array', 
#                          'categoryarray':['Hubei','Other Chinese Provinces','Rest of the World']})
fig.show()

temp = data.copy()
temp = temp[(temp["Type local"] != "Dépendance")& (temp["Type local"] != "Local industriel. commercial ou assimilé")].reset_index(drop = True)
temp['Prix mètre carré'] = temp['Valeur fonciere']/temp['Surface reelle bati']
temp['Region'] = temp.apply(location, axis=1)
temp = temp.groupby('Region')['Prix mètre carré'].mean().reset_index()
temp = temp.melt(id_vars='Region', value_vars=['Prix mètre carré'], 
                 var_name='Case', value_name='Count').sort_values('Count')
temp.head()

fig = px.bar(temp, y='Region', x='Count', color='Case', barmode='group', orientation='h',
             text='Count', title='Paris - Nord - Alpes-Maritimes', 
             color_discrete_sequence= [dth, rec, cnf])
fig.update_traces(textposition='outside')
#fig.update_layout(uniformtext_minsize=8, uniformtext_mode='hide')
fig.show()

In [24]:
carrez = data[(data["Type local"] != "Dépendance")& (data["Type local"] != "Local industriel. commercial ou assimilé")].reset_index(drop = True)
carrez["carrez_sum"] = data["Surface Carrez du 1er lot"].fillna(0)  +  data["Surface Carrez du 2eme lot"].fillna(0) + data["Surface Carrez du 3eme lot"].fillna(0) + data["Surface Carrez du 4eme lot"].fillna(0) + data["Surface Carrez du 5eme lot"].fillna(0)
carrez["Prix mètre carré"] = np.where(carrez["carrez_sum"] != 0,carrez["Valeur fonciere"]/carrez["carrez_sum"],carrez["Valeur fonciere"]/carrez["Surface reelle bati"])
carrez = carrez.drop(np.where(carrez['Prix mètre carré'] > 25000)[0])
display(carrez)


def location(row):
    if row['Code departement']=='75':
            return 'Paris'
    elif row['Code departement']=='6':
            return 'Alpes-Maritimes'
    elif row['Code departement']=='59':
        return 'Nord'
    else:
        return 'Reste de la France'


temp = carrez.sample(frac = 0.01)
temp['Region'] = temp.apply(location, axis=1)
temp['Date'] = temp['Date mutation'].dt.strftime('%Y-%m-%d')
temp = temp.groupby(['Region', 'Date'])['Prix mètre carré'].mean().reset_index()
temp = temp.melt(id_vars=['Region', 'Date'], value_vars=['Prix mètre carré'], 
                 var_name='Case', value_name='Count').sort_values('Count')
# temp = temp.sort_values(['Date', 'Region', 'Case']).reset_index()
temp.head()

fig = px.bar(temp, y='Region', x='Count', color='Case', barmode='group', orientation='h',
             text='Count', title='Hubei - China - World', animation_frame='Date',
             color_discrete_sequence= [dth, rec, cnf], range_x=[0, 15000])
fig.update_traces(textposition='outside')
# fig.update_layout(uniformtext_minsize=8, uniformtext_mode='hide')
# fig.update_layout(yaxis={'categoryorder':'array', 
#                          'categoryarray':['Hubei','Other Chinese Provinces','Rest of the World']})
fig.show()

temp = carrez.copy()
temp['Region'] = temp.apply(location, axis=1)
temp = temp.groupby('Region')['Prix mètre carré'].mean().reset_index()
temp = temp.melt(id_vars='Region', value_vars=['Prix mètre carré'], 
                 var_name='Case', value_name='Count').sort_values('Count')
temp.head()

fig = px.bar(temp, y='Region', x='Count', color='Case', barmode='group', orientation='h',
             text='Count', title='Paris - Nord - Alpes-Maritimes', 
             color_discrete_sequence= [cnf])
fig.update_traces(textposition='outside')
#fig.update_layout(uniformtext_minsize=8, uniformtext_mode='hide')
fig.show()

Date mutation  Valeur fonciere  No voie Type de voie Code voie  \
0          2018-01-03         109000.0     13.0          RUE      1660   
1          2018-01-04         239300.0      4.0          RUE      0025   
2          2018-01-04         239300.0      4.0          RUE      0025   
3          2018-01-04         239300.0      4.0          RUE      0025   
4          2018-01-04         239300.0      4.0          RUE      0025   
...               ...              ...      ...          ...       ...   
6507941    2022-12-29        1650000.0     78.0           AV      7149   
6507942    2022-11-03         291000.0    128.0          RUE      0012   
6507943    2022-12-23         934000.0      5.0          VLA      3488   
6507944    2022-12-23          70000.0     67.0          RUE      1255   
6507945    2022-12-19         525000.0      3.0          RUE      3842   

                      Voie  Code postal Code departement  Code commune  \
0              GEN LOGEROT       1000.0                1            53   
1           DE LA BARMETTE       1250.0                1            95   
2           DE LA BARMETTE       1250.0                1            95   
3           DE LA BARMETTE       1250.0                1            95   
4           DE LA BARMETTE       1250.0                1            95   
...                    ...          ...              ...           ...   
6507941        PAUL DOUMER      75016.0               75           116   
6507942   DE L ABBE GROULT      75015.0               75           115   
6507943        FAISANDERIE      75016.0               75           116   
6507944           BRANCION      75015.0               75           115   
6507945  FREDERIC MAGISSON      75015.0               75           115   

        Section  ...  Nombre de lots Code type local   Type local  \
0            AN  ...               2             2.0  Appartement   
1            AH  ...               0             1.0       Maison   
2            AH  ...               0             1.0       Maison   
3            AH  ...               0             1.0       Maison   
4            AH  ...               0             1.0       Maison   
...         ...  ...             ...             ...          ...   
6507941      DM  ...               3             2.0  Appartement   
6507942      AE  ...               1             2.0  Appartement   
6507943      EE  ...               2             2.0  Appartement   
6507944      AJ  ...               2             2.0  Appartement   
6507945      EJ  ...               2             2.0  Appartement   

         Surface reelle bati  Nombre pieces principales  Nature culture  \
0                       73.0                        4.0             NaN   
1                      163.0                        4.0               S   
2                      163.0                        4.0              AG   
3                       51.0                        2.0              AG   
4                       51.0                        2.0               S   
...                      ...                        ...             ...   
6507941                150.0                        6.0             NaN   
6507942                 35.0                        2.0             NaN   
6507943                 58.0                        2.0             NaN   
6507944                 15.0                        1.0             NaN   
6507945                 40.0                        3.0             NaN   

         Surface terrain  Nature mutation  carrez_sum Prix mètre carré  
0                    NaN              NaN         0.0      1493.150685  
1                  949.0              NaN         0.0      1468.098160  
2                  420.0              NaN         0.0      1468.098160  
3                  420.0              NaN         0.0      4692.156863  
4                  949.0              NaN         0.0      4692.156863  
...                  ...              ...         ...         

NameError: name 'df' is not defined